In [ ]:
from langchain_core.documents import Document
from langchain_community.document_loaders import PyMuPDFLoader , DirectoryLoader

dir_loader = DirectoryLoader('../data/pdf', glob='**/*.pdf', show_progress=True, loader_cls=PyMuPDFLoader)
documents = dir_loader.load()
documents

100%|██████████| 1/1 [00:02<00:00,  2.50s/it]


[Document(metadata={'producer': 'pdfTeX-1.40.15', 'creator': 'LaTeX with hyperref package', 'creationdate': '2015-06-29T10:51:25-04:00', 'source': '..\\data\\pdf\\MongoDB-manual.pdf', 'file_path': '..\\data\\pdf\\MongoDB-manual.pdf', 'total_pages': 946, 'format': 'PDF 1.5', 'title': '', 'author': '', 'subject': '', 'keywords': '', 'moddate': '2015-06-29T10:51:25-04:00', 'trapped': '', 'modDate': "D:20150629105125-04'00'", 'creationDate': "D:20150629105125-04'00'", 'page': 0}, page_content='MongoDB Documentation\nRelease 3.0.4\nMongoDB Documentation Project\nJune 29, 2015'),
 Document(metadata={'producer': 'pdfTeX-1.40.15', 'creator': 'LaTeX with hyperref package', 'creationdate': '2015-06-29T10:51:25-04:00', 'source': '..\\data\\pdf\\MongoDB-manual.pdf', 'file_path': '..\\data\\pdf\\MongoDB-manual.pdf', 'total_pages': 946, 'format': 'PDF 1.5', 'title': '', 'author': '', 'subject': '', 'keywords': '', 'moddate': '2015-06-29T10:51:25-04:00', 'trapped': '', 'modDate': "D:20150629105125-04

In [ ]:
from langchain_core.documents import Document
from langchain_community.document_loaders import PyMuPDFLoader , DirectoryLoader

dir_loader = DirectoryLoader('../data/pdf', glob='**/*.pdf', show_progress=True, loader_cls=PyMuPDFLoader)
documents = dir_loader.load()
documents

In [22]:
def chunk_documents(documents, size=500, overlap=50):
    chunks = []

    for doc in documents:
        text = doc.page_content
        metadata = doc.metadata

        start = 0
        while start < len(text):
            end = start + size
            chunk_text = text[start:end]

            chunks.append(
                Document(
                    page_content=chunk_text,
                    metadata=metadata
                )
            )

            start = end - overlap

    return chunks


In [ ]:
# def chunk_documentss(documents):
#     chunks = []

#     for doc in documents:
#         text = doc.page_content
#         metadata = doc.metadata
        
#         # Split text by '.' to get sentences
#         # The split removes the '.', so we'll need to add it back
#         sentences = text.split('.')

#         for sentence in sentences:
#             # We check if the sentence has content after stripping whitespace
#             if sentence.strip():
#                 # Re-append the period to complete the sentence
#                 chunk_text = sentence.strip() + "."
                
#                 chunks.append(
#                     Document(
#                         page_content=chunk_text,
#                         metadata=metadata
#                     )
#                 )

#     return chunks

In [23]:
chunks = chunk_documents(documents)

chunks


[Document(metadata={'producer': 'pdfTeX-1.40.15', 'creator': 'LaTeX with hyperref package', 'creationdate': '2015-06-29T10:51:25-04:00', 'source': '..\\data\\pdf\\MongoDB-manual.pdf', 'file_path': '..\\data\\pdf\\MongoDB-manual.pdf', 'total_pages': 946, 'format': 'PDF 1.5', 'title': '', 'author': '', 'subject': '', 'keywords': '', 'moddate': '2015-06-29T10:51:25-04:00', 'trapped': '', 'modDate': "D:20150629105125-04'00'", 'creationDate': "D:20150629105125-04'00'", 'page': 0}, page_content='MongoDB Documentation\nRelease 3.0.4\nMongoDB Documentation Project\nJune 29, 2015'),
 Document(metadata={'producer': 'pdfTeX-1.40.15', 'creator': 'LaTeX with hyperref package', 'creationdate': '2015-06-29T10:51:25-04:00', 'source': '..\\data\\pdf\\MongoDB-manual.pdf', 'file_path': '..\\data\\pdf\\MongoDB-manual.pdf', 'total_pages': 946, 'format': 'PDF 1.5', 'title': '', 'author': '', 'subject': '', 'keywords': '', 'moddate': '2015-06-29T10:51:25-04:00', 'trapped': '', 'modDate': "D:20150629105125-04

In [24]:
texts = [chunk.page_content for chunk in chunks]
texts

['MongoDB Documentation\nRelease 3.0.4\nMongoDB Documentation Project\nJune 29, 2015',
 '2',
 'Contents\n1\nIntroduction to MongoDB\n3\n1.1\nWhat is MongoDB . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . .\n3\n2\nInstall MongoDB\n5\n2.1\nRecommended Operating Systems for Production Deployments . . . . . . . . . . . . . . . . . . . .\n5\n2.2\nOther Supported Operating Systems . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . .\n5\n2.3\nInstallation Guides . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . .\n5\n2.4\nFi',
 '. . . . . . . . . . . . . . . . . . . . .\n5\n2.4\nFirst Steps with MongoDB . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . .\n55\n2.5\nAdditional Resources . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . .\n55\n3\nMongoDB CRUD Operations\n57\n3.1\nMongoDB CRUD Introduction\n. . . . . . . . . . . . . . . . . . . 

In [25]:
import numpy as np
from sentence_transformers import SentenceTransformer
import chromadb
from chromadb.config import Settings
import uuid
from typing import List,Dict,Any,Tuple
from sklearn.metrics.pairwise import cosine_similarity


In [26]:
class EmbeddingManager:
    def __init__(self, model_name: str = 'all-MiniLM-L6-v2'):
        """Initialize the embedding manager  
        
        Args:
            model_name: Huggingface model name for sentence embedding 
        """
        self.model_name = model_name
        self.model = None
        self._load_model()
        
    def _load_model(self):
        """Load the sentenceTransformer model """
        try:
            print(f"Loading embedding model :{self.model_name}")    
            self.model = SentenceTransformer(self.model_name)
            print("Model loaded successfully. Embedding demension: ", self.model.get_sentence_embedding_dimension())
        except Exception as e:
            print(f"Error loading model:{self.model_name} ", e)
            raise
        
        
        
    def generate_embeddings(self, texts: List[str]) -> np.ndarray:
        """Generate embeddings for a list of texts
        
        Args:
            texts: List of text strings to embed
            
        Returns:
            numpy array of embeddings with shape (len(texts), embedding_dimension)
             """
        
        if not self.model:
            raise ValueError("Embedding model is not loaded.")  
        
        print(f"Generating embeddings for {len(texts)} texts...")   
        embeddings = self.model.encode(texts, show_progress_bar=True)
        print(f"Embeddings generated successfully. Shape: {embeddings.shape}")
        return embeddings
    
    
###Intialize the embedding manager
embedding_manager = EmbeddingManager()
embedding_manager

Loading embedding model :all-MiniLM-L6-v2


Loading weights: 100%|██████████| 103/103 [00:00<00:00, 416.34it/s, Materializing param=pooler.dense.weight]                             
BertModel LOAD REPORT from: sentence-transformers/all-MiniLM-L6-v2
Key                     | Status     |  | 
------------------------+------------+--+-
embeddings.position_ids | UNEXPECTED |  | 

Notes:
- UNEXPECTED	:can be ignored when loading from different task/architecture; not ok if you expect identical arch.


Model loaded successfully. Embedding demension:  384


### vectorStore


In [27]:
import os
class VectorStore:
    """Manage document embeddings in a chromadb vector store"""
    def __init__(self, collection_name: str = 'pdf_documents', persist_directory: str = '../data/chroma_db'):
        """Initialize the vector store
        
        Args:
            collection_name: Name of the chromadb collection 
            persist_directory: Directory to persist the vector data
        """
        self.collection_name = collection_name
        self.persist_directory = persist_directory
        self.client = None
        self.collection = None
        self._initialize_store()
        
        
    def _initialize_store(self):
        """Initialize the chromadb client and collection"""
        try:
            #Create the persistent chromadb client
            os.makedirs(self.persist_directory, exist_ok=True)
            self.client = chromadb.PersistentClient(path=self.persist_directory)
            
            #Get or create the collection
            self.collection = self.client.get_or_create_collection(
                name=self.collection_name,
                metadata={"description": "PDF Document embeddings for Rag"} 
            )
            print(f"Vector store initialized successfully. Collection: {self.collection_name}")
            print(f"Persist directory: {self.collection.count()}")
            
        except Exception as e:
            print(f"Error initializing vector store: {e}")
            raise
        
    def add_documents(self, documents: List[Any], embedding: np.ndarray):
        """Add documents and their embeddings to the vector store
        
        Args:
            documents: List of Document objects to add
            embedding_manager: Instance of EmbeddingManager to generate embeddings
        """
        if len(documents)!=len(embedding):
            raise ValueError("Number of documents and embeddings must match.")
        print(f"Adding {len(documents)} documents to vector store...")
        
        
        ids = []
        metadatas = []
        documents_texts = []
        embeddings_list = []
        for i ,(doc, embedding) in enumerate(zip(documents, embedding)):
            doc_id = f"doc_{uuid.uuid4().hex[:8]}_{i}"
            ids.append(doc_id)
            metadata = dict(doc.metadata)
            metadata['doc_index'] = i
            metadatas.append(metadata)
            documents_texts.append(doc.page_content)
            embeddings_list.append(embedding.tolist())
            
            
        try:
            self.collection.add(
                ids=ids,
                embeddings=embeddings_list,
                metadatas=metadatas,
                documents=documents_texts
            )
            print(f"Successfully added {len(documents)} documents to vector store.")
            print(f"Documents added successfully. Total documents in store: {self.collection.count()}")
        
        
        except Exception as e:
            print(f"Error adding documents to vector store: {e}")
            raise
        
vector_store = VectorStore()
vector_store

Vector store initialized successfully. Collection: pdf_documents
Persist directory: 5113


In [28]:
embedding_manager = EmbeddingManager()
embeddingmanager = embedding_manager.generate_embeddings(texts)
vector_store.add_documents(chunks, embeddingmanager)

Loading embedding model :all-MiniLM-L6-v2


Loading weights: 100%|██████████| 103/103 [00:00<00:00, 411.06it/s, Materializing param=pooler.dense.weight]                             
BertModel LOAD REPORT from: sentence-transformers/all-MiniLM-L6-v2
Key                     | Status     |  | 
------------------------+------------+--+-
embeddings.position_ids | UNEXPECTED |  | 

Notes:
- UNEXPECTED	:can be ignored when loading from different task/architecture; not ok if you expect identical arch.


Model loaded successfully. Embedding demension:  384
Generating embeddings for 5113 texts...


Batches: 100%|██████████| 160/160 [01:40<00:00,  1.59it/s]


Embeddings generated successfully. Shape: (5113, 384)
Adding 5113 documents to vector store...
Successfully added 5113 documents to vector store.
Documents added successfully. Total documents in store: 10226


### Retriever pipeline from vectorstore

In [29]:
class RAGRetriever:
    """Handles query-based retrieval from the vector store"""
    
    def __init__(self, vector_store:VectorStore, embedding_manager:EmbeddingManager):
        """
        Initialize the retriever
        
        Args:
        vector_store:Vector store containing document embeddingd
        embedding_manager: Embedding manager to generate query embeddings
        """
        self.vector_store = vector_store
        self.embedding_manager = embedding_manager
        
        
    def retrieve(self, query: str, top_k: int = 5, score_threshold: float = 0.0) -> List[Document]:
        """Retrive relevant documents for a given query
        Args:
            query: User query string
            top_k: Number of top relevant documents to retrieve
            score_threshold: Minimum similarity score for retrieved documents
            
        Returns:
            List of dictionaries containing retrieved documents and their metadata       
        """
        print(f"Retrieving documents for query: '{query}' with top_k={top_k} and score_threshold={score_threshold}")
        query_embedding = self.embedding_manager.generate_embeddings([query])[0]
        
        try:
            results = self.vector_store.collection.query(
                query_embeddings=[query_embedding.tolist()],
                n_results=top_k
            )
            retrieved_docs = []
            if results['documents'] and results['documents'][0]:
                documents = results['documents'][0]
                metadatas = results['metadatas'][0]
                distances = results['distances'][0]
                ids = results['ids'][0]
                
                
                for i,(doc_id,document,metadata,distance) in enumerate(zip(ids,documents,metadatas,distances)):
                    similarity_score = 1 - distance
                    if similarity_score >= score_threshold:
                        retrieved_docs.append({
                            'id': doc_id,
                            'document': document,
                            'metadata': metadata,
                            'similarity': similarity_score,
                            'distance': distance,
                            'rank': i+1
                        })
                         
                print(f"Retrieved {len(retrieved_docs)} documents for query: '{query}'")
            else:
                print("No documents found")
    
    
            return retrieved_docs
        except Exception as e:
            print(f"Error during retrieval:{e}")
            return []


ragretriever =  RAGRetriever(vector_store,embedding_manager)

In [30]:
ragretriever

In [31]:
a= ragretriever.retrieve("collection")


Retrieving documents for query: 'collection' with top_k=5 and score_threshold=0.0
Generating embeddings for 1 texts...


Batches: 100%|██████████| 1/1 [00:00<00:00, 132.05it/s]

Embeddings generated successfully. Shape: (1, 384)
Retrieved 4 documents for query: 'collection'


In [32]:
a

[{'id': 'doc_3aa841bc_24',
  'document': ' MongoDB',
  'metadata': {'format': 'PDF 1.5',
   'author': '',
   'subject': '',
   'modDate': "D:20150629105125-04'00'",
   'creator': 'LaTeX with hyperref package',
   'title': '',
   'page': 7,
   'doc_index': 24,
   'file_path': '..\\data\\pdf\\MongoDB-manual.pdf',
   'producer': 'pdfTeX-1.40.15',
   'keywords': '',
   'creationDate': "D:20150629105125-04'00'",
   'total_pages': 946,
   'source': '..\\data\\pdf\\MongoDB-manual.pdf',
   'trapped': '',
   'creationdate': '2015-06-29T10:51:25-04:00',
   'moddate': '2015-06-29T10:51:25-04:00'},
  'similarity': 0.03410762548446655,
  'distance': 0.9658923745155334,
  'rank': 1},
 {'id': 'doc_730468e1_24',
  'document': ' MongoDB',
  'metadata': {'author': '',
   'source': '..\\data\\pdf\\MongoDB-manual.pdf',
   'creationdate': '2015-06-29T10:51:25-04:00',
   'modDate': "D:20150629105125-04'00'",
   'trapped': '',
   'total_pages': 946,
   'file_path': '..\\data\\pdf\\MongoDB-manual.pdf',
   'fo

### INTEGRATION  VECTORDB CONTEXT PIPELINE WITH LLM OUPUT


In [77]:
from langchain_groq import ChatGroq
import os 
from dotenv import load_dotenv
load_dotenv()
api_key = os.getenv("GROQ-API-KEY")
llm = ChatGroq(groq_api_key=api_key,model="openai/gpt-oss-120b", temperature=0.1,max_tokens=1024)


def rag_simple(query,retriever,llm,top_k=5):
    
    results = retriever.retrieve(query, top_k=top_k)
    context = "\n\n".join([doc['document'] for doc in results]) if results else""
    if not context:
        return "No relevant information found in the documents."
    
    
    ##generate the answer using GROQ LLM
    prompt = f"""Use the following context to answer the question concisely
    Context : {context}
    
    Question: {query}
    Answer"""
    print("------------------------------------------------------------------\n" + prompt)
    print("------------------------------------------------------------------\n")
    response =llm.invoke(prompt)
    return response.content

In [79]:
answer =rag_simple("what is collection", ragretriever, llm)
print(answer)

Retrieving documents for query: 'what is collection' with top_k=5 and score_threshold=0.0
Generating embeddings for 1 texts...


Batches: 100%|██████████| 1/1 [00:00<00:00, 56.25it/s]

Embeddings generated successfully. Shape: (1, 384)
Retrieved 5 documents for query: 'what is collection'
------------------------------------------------------------------
Use the following context to answer the question concisely
    Context : ema. Collections do not enforce document structure. Decisions that affect how
you model data can affect application performance and database capacity. See Data Modeling Concepts (page 145)
for a full high level overview of data modeling in MongoDB.
This document describes a data model that uses references (page 147) between documents to describe relationships
between connected data.
Pattern
Consider the following example that maps publisher and book relationships. The example illustrates the adv

ema. Collections do not enforce document structure. Decisions that affect how
you model data can affect application performance and database capacity. See Data Modeling Concepts (page 145)
for a full high level overview of data modeling in MongoDB.
This

A **collection** in MongoDB is a grouping of documents (records) stored together within a database. It is analogous to a table in relational databases, but unlike tables, collections do not enforce a fixed schema—each document in the collection can have a different structure.
